# Rasters 2: Overlays

## Overview


1. Read in a raster file in GeoTIFF format of surface elevation using the Rioxarray package
1. Explore the attributes of the GeoTIFF file
1. Plot the GeoTIFF using Matplotlib and Cartopy
1. Overlay the GeoTIFF on a plot of realtime forecast reflectivity data


## Prerequisites

| Concepts | Importance | Notes |
| --- | --- | --- |
| Rasters 1| Necessary | |

* **Time to learn**: 30 minutes
***

<div class="alert alert-warning">WARNING: due to the high-resolutions of both the raster image and the HRRR forecast reflectivity, this notebook will use approx. 8GB of system memory as you run it! You may wish to simply use this already-populated notebook as a reference, and only modify/run through it when you need to. 
    <br><b>Be sure to <i>close and shutdown</i> the notebook when finished!</b>
</div>

## Imports

In [ ]:
from datetime import datetime, timedelta
import pandas as pd
import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import cartopy.feature as cfeat
import numpy as np
import xarray as xr

from metpy.plots import USCOUNTIES
from metpy.plots import ctables
import rioxarray as rio
from matplotlib.colors import BoundaryNorm
from matplotlib.ticker import MaxNLocator

<div class="alert alert-info"><b>Note:</b> Besides the <code>rioxarray</code> library, we've also imported <b>USCOUNTIES</b> from MetPy. This allows for the plotting of US county line boundaries, similar to other Cartopy cartographic features such as states.<br>
Additonally, we've imported a set of <a href=https://unidata.github.io/MetPy/latest/api/generated/metpy.plots.ctables.html>color tables</a>, also from MetPy.<br>
We've also imported a couple additional methods from Matplotlib, which we'll use to customize the look of our plot when using the <code>imshow</code> method.
</div>

## Read in a raster file in GeoTIFF format

Process the topography GeoTIFF file, downloaded from Natural Earth, using the [rioxarray](https://corteva.github.io/rioxarray/stable/#) package. This package provides an xarray interface while also presenting functionality similar to the [rasterio](https://rasterio.readthedocs.io/) library.

In [ ]:
msr = rio.open_rasterio('/spare11/atm533/data/raster/US_MSR_10M/US_MSR.tif')

Explore the GeoTIFF file. Remember, it's a TIFF file that is georeferenced.

In [ ]:
msr

<div class="alert alert-info"><b>Note:</b> 
    <b>rioxarray</b> returns a DataArray that has a unique coordinate variable, <code>spatial_ref</code>. This coordinate variable's attributes includes CRS info in what's called <b>well-known text (WKT)</b> format, as well as the <i>Affine transformation</i> parameters. See references at the end of this notebook.
</div>

Get the bounding box coordinates of the raster file. We will need to pass them to Matplotlib's `imshow` function.

In [ ]:
left,bottom,right,top = msr.rio.bounds()
left,bottom,right,top

These values represent the coordinates, <i>in units specific to the GeoTIFF's geographic coordinate reference system</i>, of the lower-left and upper-right corners of the raster file.

Get the projection info, which we can later use in Cartopy. A rioxarray dataset object has an attribute called `crs` for this purpose.

In [ ]:
msr.rio.crs

Assign this CRS to a Cartopy projection object.

In [ ]:
projMSR = ccrs.epsg('3857')

<div class="alert alert-info"><b>Note:</b> What does this coordinate reference system refer to? It is called <a href="https://en.wikipedia.org/wiki/Web_Mercator_projection"><i>Web Mercator</i></a>, aka Pseudo Mercator, which is what is used in most web-based interactive mapping applications, such as Google Earth. See <a href=http://epsg.io/3857>https://epsg.io/3857</a> </dev>

Examine the `spatial_ref` attribute of this Dataset.

In [ ]:
msr.spatial_ref

This information makes it possible for GIS applications, such as Cartopy, to transform data that's represented in one CRS to another.

Select the first (and only) band and redefine the DataArray object, so it only has dimensions of x and y.

In [ ]:
msr = msr.sel(band=1)

Determine the min and max values. 

In [ ]:
msr.min(),msr.max()

<div class="alert alert-info"><b>Note:</b> For this raster file, the values (which were manually determined by its author) are <i>inversely proportional</i> to elevation. Thus, lower values correspond to higher elevation.</div>

The next cell will determine how the topography field will be displayed on the figure. These settings work well for this dataset, but obviously must be customized for use with other raster images. This is akin to setting contour fill intervals, but instead of using Matplotlib's `contourf` method, we will use `imshow`, and take advantage of the two Matplotlib methods we imported at the start of the notebook.

In [ ]:
# Pick a binning (which is analagous to the # of fill contours, and set a min/max range)
levels = MaxNLocator(nbins=30).tick_values(msr.min(), msr.max()-20)

# Pick the desired colormap, sensible levels, and define a normalization
# instance which takes data values and translates those into levels.
# In this case, we take a color map of 256 discrete colors and normalize them down to 30.
cmap = plt.get_cmap('gist_gray')
norm = BoundaryNorm(levels, ncolors=cmap.N, clip=True)

Examine the levels.

In [ ]:
levels

## Plot the GeoTIFF using Matplotlib and Cartopy

Create a region over which we will plot ... in this case, centered over NY State.

In [ ]:
latN_sub = 45.2
latS_sub = 40.2
lonW_sub = -80.0
lonE_sub = -71.5
cLat_sub = (latN_sub + latS_sub)/2.
cLon_sub = (lonW_sub + lonE_sub )/2.

proj_sub = ccrs.LambertConformal(central_longitude=cLon_sub,
                             central_latitude=cLat_sub,
                             standard_parallels=[cLat_sub])

Plot the GeoTIFF using `imshow`. Just as we've previously transformed data from PlateCarree (lat/lon), here we transform from the Web Mercator projection that the elevation raster file uses.

In [ ]:
res = '50m' # Use the medium resolution Natural Earth shapefiles so plotting goes a bit faster than with the highest (10m)
fig = plt.figure(figsize=(18,12))
ax = plt.subplot(1,1,1,projection=proj_sub)
ax.set_extent((lonW_sub,lonE_sub,latS_sub,latN_sub),crs=ccrs.PlateCarree())
ax.add_feature (cfeat.LAND.with_scale(res))
ax.add_feature (cfeat.OCEAN.with_scale(res))
ax.add_feature(cfeat.COASTLINE.with_scale(res))
ax.add_feature (cfeat.LAKES.with_scale(res), alpha = 0.5)
ax.add_feature (cfeat.STATES.with_scale(res))
ax.add_feature(USCOUNTIES,edgecolor='grey', linewidth=1 );
im = ax.imshow(msr,cmap=plt.get_cmap('gist_gray'),
                 alpha=0.4,norm=norm,transform=projMSR, zorder=10)

<div class="alert alert-danger"><b>WTF! </b>Well ... that does not seem to accurately represent the topography in the NE US!
    One additional parameter we must pass into <code>imshow</code> is <i>extent</i>. The default values are not what we want; instead, we use the Bounding Box values that we read in earlier. See the documentation for <i>extent</i> in <code>imshow</code>'s documentation.</div>

In [ ]:
res = '50m'
fig = plt.figure(figsize=(18,12))
ax = plt.subplot(1,1,1,projection=proj_sub)
ax.set_extent((lonW_sub,lonE_sub,latS_sub,latN_sub),crs=ccrs.PlateCarree())
ax.add_feature (cfeat.LAND.with_scale(res))
ax.add_feature (cfeat.OCEAN.with_scale(res))
ax.add_feature(cfeat.COASTLINE.with_scale(res))
ax.add_feature (cfeat.LAKES.with_scale(res), alpha = 0.5)
ax.add_feature (cfeat.STATES.with_scale(res))
ax.add_feature(USCOUNTIES,edgecolor='grey', linewidth=1)
# Pass in the bounding box coordinates as the value for extent
im = ax.imshow(msr, extent = [left,right,bottom,top],cmap=plt.get_cmap('gist_gray'),
                 alpha=0.4,norm=norm,transform=projMSR);

That's more like it! Now, we can plot maps that include one (or more) GeoTIFF raster images, while also overlaying meteorological data, such as point observations or gridded model output.

## Overlay the GeoTIFF on a plot of realtime forecast reflectivity data

Below, we go through the same steps that we did in the first Raster notebook to gather the latest HRRR model output, but plot filled contours of forecasted 1km above ground level radar reflectivity over the background of topography. We'll plot over the CONUS.

In [ ]:
now = datetime.now()
year = now.year
month = now.month
day = now.day
hour = now.hour
minute = now.minute
print (year, month, day, hour,minute)

if (minute < 45): 
    hrDelta = 3
else:
    hrDelta = 2
runTime = now - timedelta(hours=hrDelta)
runTimeStr = runTime.strftime('%Y%m%d %H00 UTC')
modelDate = runTime.strftime('%Y%m%d')
modelHour = runTime.strftime('%H')
modelDay = runTime.strftime('%D')
print (modelDay)
print (modelHour)
print (runTimeStr)

In [ ]:
data_url = 'https://thredds.ucar.edu/thredds/dodsC/grib/NCEP/HRRR/CONUS_2p5km/HRRR_CONUS_2p5km_'+ modelDate + '_' + modelHour + '00.grib2'

In [ ]:
ds = xr.open_dataset(data_url)

In [ ]:
refl = ds.Reflectivity_height_above_ground

In [ ]:
refl

Select the time index (corresponding to the forecast hour; index 0 corresponds to the analysis time) and the (single) height index. 

In [ ]:
idxTime = 0
idxHght = 0
validTime = refl.time1.isel(time1 = idxTime).values # Returns validTime as a NumPy Datetime 64 object
validTime = pd.Timestamp(validTime) # Converts validTime to a Pandas Timestamp object
timeStr = validTime.strftime("%Y-%m-%d %H%M UTC") # We can now use Datetime's strftime method to create a time string.
tl1 = "HRRR 1km AGL Reflectivity (dBZ)"
tl2 = str('Valid at: '+ timeStr)
title_line = (tl1 + '\n' + tl2 + '\n')

<div class="alert alert-warning"><b>Note:</b> The names of some of the coordinate variables, particularly the vertical and time ones, can vary from run-to-run. Although MetPy's Xarray accessor has a clever means of dealing with that, for now, pay attention to the names of the coordinate variables and substitute when necessary. </dev>

In [ ]:
refl = ds.Reflectivity_height_above_ground.isel(time1=idxTime, height_above_ground1=idxHght)

Get the projection info from the HRRR Dataset

In [ ]:
proj = ds.LambertConformal_Projection

lat1 = proj.latitude_of_projection_origin
lon1 = proj.longitude_of_central_meridian
slat = proj.standard_parallel
projHRRR = ccrs.LambertConformal(central_longitude=lon1,
                             central_latitude=lat1,
                             standard_parallels=[slat])

Use a set of color tables that mimics what the National Weather Services uses for its reflectivity plots.

In [ ]:
ref_norm, ref_cmap = ctables.registry.get_with_steps('NWSReflectivity', 5, 5)

In [ ]:
refl_range = np.arange(5,80,5)

<div class="alert alert-warning"><b>Be units-aware!</b>
Since we will be using Matplotlib's `contourf` method, we need to pass in the x- and y- coordinates. In the HRRR dataset we obtained from the THREDDS server, these coordinates are in units of kilometers. For a projection such as Lambert Conformal Conic, the units need to be in meters. We could simply mulptiply the x- and y- coordinate arrays by 1000, but in this case, let's have MetPy do the unit translation for us.</div>

In [ ]:
x = refl.x.metpy.convert_units('m')
y = refl.y.metpy.convert_units('m')

Make the map. 

<div class="alert alert-warning"><b>Note:</b>
    <ol><li>For speed, choose the coarsest resolution for the cartographic features. It's fine for a larger view such as the CONUS.</li>
    <li>For readability, do not plot county outlines for a regional extent as large as the CONUS</li>
        <li>This step is <b>particularly memory-intensive</b>, since we are reading in two high-resolution rasters (elevation and reflectivity)!
    </ol>
</div>

In [ ]:
res = '110m'
fig = plt.figure(figsize=(18,12))
ax = plt.subplot(1,1,1,projection=projHRRR)
ax.set_extent((-125,-68,20,52),crs=ccrs.PlateCarree())
ax.add_feature (cfeat.LAND.with_scale(res))
ax.add_feature (cfeat.OCEAN.with_scale(res))
ax.add_feature(cfeat.COASTLINE.with_scale(res))
ax.add_feature (cfeat.LAKES.with_scale(res), alpha = 0.5)
ax.add_feature (cfeat.STATES.with_scale(res))
# Usually avoid plotting counties once the regional extent is large
#ax.add_feature(USCOUNTIES,edgecolor='grey', linewidth=1 );
im = ax.imshow(msr,extent=[left, right, bottom, top],cmap=plt.get_cmap('gist_gray'),
                 alpha=0.4,norm=norm,transform=projMSR)
CF = ax.contourf(x,y,refl,levels=refl_range,cmap=ref_cmap,alpha=0.5,transform=projHRRR)
cbar = plt.colorbar(CF,fraction=0.046, pad=0.03,shrink=0.5)
cbar.ax.tick_params(labelsize=10)
cbar.ax.set_ylabel("Reflectivity (dBZ)",fontsize=10);
title = ax.set_title(title_line,fontsize=16)

---
## Summary
* The Rioxarray package allows for raster-specific methods on geo-referenced Xarray objects. 
* When using `imshow` with Cartopy's geo-referenced axes in Matplotlib, one must specify the `extent`, derived from the GeoTIFF's bounding box.
* GeoTIFFs can be overlayed with other geo-referenced datasets, such as gridded fields or point observations.
* The higher the resolution, the higher the memory usage.

### What's Next?
In the next notebook, we'll take a look at a multi-band GeoTIFF that is optimized for cloud storage.

## References
1. [US Counties in MetPy](https://unidata.github.io/MetPy/latest/examples/plots/US_Counties.html?highlight=uscounties)
1. [CRS definitions](https://www.earthdatascience.org/courses/use-data-open-source-python/intro-vector-data-python/spatial-data-vector-shapefiles/epsg-proj4-coordinate-reference-system-formats-python)
1. WKT definitions:<br>
    a. [From opengeospatial.org](https://docs.opengeospatial.org/is/18-010r7/18-010r7.html)<br>
    b. [From Wikipedia](https://en.wikipedia.org/wiki/Well-known_text_representation_of_coordinate_reference_systems)
1. Affine transformation defs:<br>
    a. [From Wikipedia](https://en.wikipedia.org/wiki/Affine_transformation)<br>
    b. [From Univ of Minnesota GIS Course](https://giscourses.cfans.umn.edu/sites/giscourses.cfans.umn.edu/files/5480chapter4_tranf_excerpt.pdf)
1. [imshow's documentation](https://matplotlib.org/api/_as_gen/matplotlib.pyplot.imshow.html)